In [ ]:
import os
import numpy as np
import moviepy.editor as mp
from googletrans import Translator
from gtts import gTTS
import subprocess
from TTS.api import TTS
import torch
from IPython.display import Audio, display
import whisper
import librosa
import soundfile as sf
from moviepy.editor import TextClip
from moviepy.editor import CompositeVideoClip
import soundfile as sf
from moviepy.editor import VideoFileClip, AudioFileClip, TextClip, CompositeVideoClip
import re
from PIL import ImageFont

ruta_carpeta_principal = "C://Users//R20//Desktop//videostraduccidos//"
ruta_carpeta_audios_esp = "audios_creados//audio_esp.wav"
ruta_carpeta_audios_ing = "audios_creados//audio_ing.wav"
ruta_carpeta_audios_fin = "audios_creados//audio_fin.wav"
ruta_carpeta_videofin = "videos_creados//video3.mp4"
nombre_video = "videos_descargados//video1.mp4"

rutaVideo = ruta_carpeta_principal + nombre_video
rutaAudioIngles = ruta_carpeta_principal + ruta_carpeta_audios_ing
rutaAudioGenerado =  ruta_carpeta_principal + ruta_carpeta_audios_esp
rutaAudioGeneradoNuevaVelocidad = ruta_carpeta_principal + ruta_carpeta_audios_fin
ruta_video_final = ruta_carpeta_principal + ruta_carpeta_videofin

In [ ]:
model = whisper.load_model("base")
result = model.transcribe(rutaVideo)

whisper_text = result["text"]
whisper_language = result['language']

print("Audio text:", whisper_text)

target_language = "Spanish" 
# Mapping between full names and ISO 639-1 codes
language_mapping = {'English': 'en', 'Spanish': 'es', 'Chinese (Simplified)': 'zh-cn'}

target_language_code = language_mapping[target_language]
from googletrans import Translator
translator = Translator()
translated_text = translator.translate(whisper_text, src=whisper_language, dest=target_language_code).text
print("Translated text:", translated_text)



In [ ]:
# Confirmar la licencia
confirmation = input("You must confirm the licensing terms. Do you agree? (y/n): ")
if confirmation.lower() != 'y':
    print("Exiting. License agreement not accepted.")
    exit()

# Crear instancia de TTS
tts = TTS("tts_models/multilingual/multi-dataset/xtts_v2").to("cuda")

video = mp.VideoFileClip(rutaVideo)
audio_clip = video.audio
audio_clip.write_audiofile(rutaAudioIngles)

# Generar audio
tts.tts_to_file(
    translated_text,
    speaker_wav=rutaAudioIngles,
    file_path=rutaAudioGenerado,
    language=target_language_code
)

In [11]:
translated_text = translated_text.replace('.', '. ').replace('?', '? ')

y_original, sr_original = librosa.load(rutaAudioIngles)
y_generated, sr_generated = librosa.load(rutaAudioGenerado)
speed_ratio = 1.45#sr_original/sr_generated  
sr_adjusted = int(sr_original * speed_ratio) 
y_adjusted = librosa.effects.time_stretch(y_generated, rate=speed_ratio)

sf.write(rutaAudioGeneradoNuevaVelocidad, y_adjusted, sr_original)

# Mostrar el audio
audio_widget = Audio(filename=rutaAudioGeneradoNuevaVelocidad, autoplay=False)
display(audio_widget)

In [9]:
video = mp.VideoFileClip(rutaVideo)

# Cargar el audio en español
audio_spanish = mp.AudioFileClip(rutaAudioGeneradoNuevaVelocidad)

# Split the translated text into words
words = translated_text.split()

# Group the words into pairs
#subtitle_lines = [' '.join(words[i:i+2]) for i in range(0, len(words), 2)]
subtitle_lines = []
for i in range(0, len(words), 2):
    if len(words[i]) > 8:
        subtitle_lines.append(words[i])
        subtitle_lines.append(words[i+1])
    else:
        subtitle_lines.append(' '.join([words[i], words[i+1]]))



# Remove any empty strings from the list of subtitle lines
subtitle_lines = [line.strip() for line in subtitle_lines if line.strip()]

# Create a list to store the text clips
subtitle_clips = []

# Set the font size and duration for each subtitle line
fontsize = 35
# Register the font
#font = ImageFont.truetype("Bubblegum.ttf", fontsize)
duration = video.duration / len(subtitle_lines)

# Initialize a variable to keep track of the current line number
line_number = 0

# Create a TextClip for each subtitle line and add it to the list
for i, line in enumerate(subtitle_lines):
    line = line.upper()
    if line_number % 3 == 0:
        color = 'red'
    elif line_number % 3 == 1:
        color = 'yellow'
    else:
        color = 'white'

    subtitle = TextClip(line, fontsize=fontsize,font="Super Disco Personal Use.ttf", color=color, bg_color='black')
    subtitle_clip = subtitle.set_pos('center').set_duration(duration).set_start(i * duration)
    subtitle_clips.append(subtitle_clip)

    # Increment the line number
    line_number += 1

# Overlay the subtitle clips on the video clip
video_with_subtitles = CompositeVideoClip([video] + subtitle_clips)

# Set the audio of the composite clip
video_with_subtitles.audio = audio_spanish

# Save the resulting clip
video_with_subtitles.write_videofile(ruta_video_final)

KeyboardInterrupt: 